In [10]:
!pip install pydub mutagen pytaglib

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 193.6/193.6 KB 2.1 MB/s eta 0:00:00a 0:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 894.4/894.4 KB 4.0 MB/s eta 0:00:0000:0100:01


In [11]:
from pydub import AudioSegment
from pydub.utils import mediainfo
import taglib
import os

def make_mono(in_file, out_file):
    sound = AudioSegment.from_wav(in_file)
    sound = sound.set_channels(1)
    tags = mediainfo(in_file).get('TAG', {})
    tags['TRACKNUMBER'] = tags['track']
    print(in_file)
    sound.export(out_file, format="wav")
    with taglib.File(out_file, save_on_exit=True) as song:
        song.tags = tags
    print(mediainfo(out_file))

for file in os.listdir('../seth/wavs'):
    make_mono("../seth/wavs/"+file, "../sethmono/wavs/"+file)

../seth/wavs/SK001-0001.wav
{'index': '0', 'codec_name': 'pcm_s16le', 'codec_long_name': 'PCM signed 16-bit little-endian', 'profile': 'unknown', 'codec_type': 'audio', 'codec_tag_string': '[1][0][0][0]', 'codec_tag': '0x0001', 'sample_fmt': 's16', 'sample_rate': '22050', 'channels': '1', 'channel_layout': 'unknown', 'bits_per_sample': '16', 'id': 'N/A', 'r_frame_rate': '0/0', 'avg_frame_rate': '0/0', 'time_base': '1/22050', 'start_pts': 'N/A', 'start_time': 'N/A', 'duration_ts': '169216', 'duration': '7.674195', 'bit_rate': '354171', 'max_bit_rate': 'N/A', 'bits_per_raw_sample': 'N/A', 'nb_frames': 'N/A', 'nb_read_frames': 'N/A', 'nb_read_packets': 'N/A', 'DISPOSITION': {'default': '0', 'dub': '0', 'original': '0', 'comment': '0', 'lyrics': '0', 'karaoke': '0', 'forced': '0', 'hearing_impaired': '0', 'visual_impaired': '0', 'clean_effects': '0', 'attached_pic': '0', 'timed_thumbnails': '0'}, 'filename': '../sethmono/wavs/SK001-0001.wav', 'nb_streams': '1', 'nb_programs': '0', 'format_

In [1]:
import os

# Trainer: Where the ✨️ happens.
# TrainingArgs: Defines the set of arguments of the Trainer.
from trainer import Trainer, TrainerArgs

# GlowTTSConfig: all model related values for training, validating and testing.
from TTS.tts.configs.vits_config import VitsConfig

# BaseDatasetConfig: defines name, formatter and path of the dataset.
from TTS.tts.configs.shared_configs import BaseDatasetConfig
from TTS.tts.datasets import load_tts_samples
from TTS.tts.models.vits import Vits
from TTS.tts.utils.text.tokenizer import TTSTokenizer
from TTS.utils.audio import AudioProcessor

# we use the same path as this script as our training folder.
output_path = os.path.dirname(os.path.abspath('../../TTS'))

# DEFINE DATASET CONFIG
# Set LJSpeech as our target dataset and define its path.
# You can also use a simple Dict to define the dataset and pass it to your custom formatter.
dataset_config = BaseDatasetConfig(
    formatter="ljspeech", meta_file_train="metadata.csv", path=os.path.join(output_path, "SethVoice/sethmono")
)

# INITIALIZE THE TRAINING CONFIGURATION
# Configure the model. Every config class inherits the BaseTTSConfig.
config = VitsConfig(
    datasets=[dataset_config],
)

# INITIALIZE THE AUDIO PROCESSOR
# Audio processor is used for feature extraction and audio I/O.
# It mainly serves to the dataloader and the training loggers.
ap = AudioProcessor.init_from_config(config)

# INITIALIZE THE TOKENIZER
# Tokenizer is used to convert text to sequences of token IDs.
# If characters are not defined in the config, default characters are passed to the config
tokenizer, config = TTSTokenizer.init_from_config(config)

# LOAD DATA SAMPLES
# Each sample is a list of ```[text, audio_file_path, speaker_name]```
# You can define your custom sample loader returning the list of samples.
# Or define your custom formatter and pass it to the `load_tts_samples`.
# Check `TTS.tts.datasets.load_tts_samples` for more details.
train_samples, eval_samples = load_tts_samples(
    dataset_config,
    eval_split=True,
    eval_split_max_size=config.eval_split_max_size,
    eval_split_size=config.eval_split_size,
)

# INITIALIZE THE MODEL
# Models take a config object and a speaker manager as input
# Config defines the details of the model like the number of layers, the size of the embedding, etc.
# Speaker manager is used by multi-speaker models.
model = Vits(config, ap, tokenizer, speaker_manager=None)

# INITIALIZE THE TRAINER
# Trainer provides a generic API to train all the 🐸TTS models with all its perks like mixed-precision training,
# distributed training, etc.
trainer = Trainer(
    TrainerArgs(), config, output_path, model=model, train_samples=train_samples, eval_samples=eval_samples
)

# AND... 3,2,1... 🚀
trainer.fit()

 > Setting up Audio Processor...
 | > sample_rate:22050
 | > resample:False
 | > num_mels:80
 | > log_func:np.log10
 | > min_level_db:0
 | > frame_shift_ms:None
 | > frame_length_ms:None
 | > ref_level_db:None
 | > fft_size:1024
 | > power:None
 | > preemphasis:0.0
 | > griffin_lim_iters:None
 | > signal_norm:None
 | > symmetric_norm:None
 | > mel_fmin:0
 | > mel_fmax:None
 | > pitch_fmin:None
 | > pitch_fmax:None
 | > spec_gain:20.0
 | > stft_pad_mode:reflect
 | > max_norm:1.0
 | > clip_norm:True
 | > do_trim_silence:False
 | > trim_db:60
 | > do_sound_norm:False
 | > do_amp_to_db_linear:True
 | > do_amp_to_db_mel:True
 | > do_rms_norm:False
 | > db_level:None
 | > stats_path:None
 | > base:10
 | > hop_length:256
 | > win_length:1024
 | > Found 485 files in /root/tts-output/SethVoice/sethmono


 > Training Environment:
 | > Backend: Torch
 | > Mixed precision: False
 | > Precision: float32
 | > Current device: 0
 | > Num. of GPUs: 1
 | > Num. of CPUs: 24
 | > Num. of Torch Threads: 12
 | > Torch seed: 54321
 | > Torch CUDNN: True
 | > Torch CUDNN deterministic: False
 | > Torch CUDNN benchmark: False
 | > Torch TF32 MatMul: False
 > Start Tensorboard: tensorboard --logdir=output/run-July-27-2023_05+40PM-0000000

 > Model has 83046892 parameters

 > EPOCH: 0/1000
 --> output/run-July-27-2023_05+40PM-0000000




> DataLoader initialization
| > Tokenizer:
	| > add_blank: True
	| > use_eos_bos: False
	| > use_phonemes: False
| > Number of instances : 481



 > TRAINING (2023-07-27 17:40:38) 


 | > Preprocessing samples
 | > Max text length: 170
 | > Min text length: 21
 | > Avg text length: 98.32640332640332
 | 
 | > Max audio length: 226717.0
 | > Min audio length: 35994.0
 | > Avg audio length: 132844.37006237006
 | > Num. instances discarded samples: 0
 | > Batch group size: 0.
eight. The press yard.

 [!] Character '\n' not found in the vocabulary. Discarding it.


...


  --> EVAL PERFORMANCE
     | > avg_loader_time: 0.03144240379333496 (+0.0)
     | > avg_loss_disc: 2.496586322784424 (+0.0)
     | > avg_loss_disc_real_0: 0.15853607654571533 (+0.0)
     | > avg_loss_disc_real_1: 0.18487492203712463 (+0.0)
     | > avg_loss_disc_real_2: 0.2728225886821747 (+0.0)
     | > avg_loss_disc_real_3: 0.2952892482280731 (+0.0)
     | > avg_loss_disc_real_4: 0.2429572194814682 (+0.0)
     | > avg_loss_disc_real_5: 0.31358301639556885 (+0.0)
     | > avg_loss_0: 2.496586322784424 (+0.0)
     | > avg_loss_gen: 2.320730209350586 (+0.0)
     | > avg_loss_kl: 3.00808048248291 (+0.0)
     | > avg_loss_feat: 4.189448356628418 (+0.0)
     | > avg_loss_mel: 25.487693786621094 (+0.0)
     | > avg_loss_duration: 1.7853946685791016 (+0.0)
     | > avg_loss_1: 36.791343688964844 (+0.0)


 > EPOCH: 998/1000
 --> output/run-July-27-2023_05+40PM-0000000

 > TRAINING (2023-07-28 00:41:03) 

   --> TIME: 2023-07-28 00:41:13 -- STEP: 7/16 -- GLOBAL_STEP: 15975
     | > loss_disc

 | > Synthesizing test sentences.



  --> EVAL PERFORMANCE
     | > avg_loader_time: 0.03568744659423828 (+0.0)
     | > avg_loss_disc: 2.4839155673980713 (+0.0)
     | > avg_loss_disc_real_0: 0.22773629426956177 (+0.0)
     | > avg_loss_disc_real_1: 0.2435954362154007 (+0.0)
     | > avg_loss_disc_real_2: 0.1826636791229248 (+0.0)
     | > avg_loss_disc_real_3: 0.20033419132232666 (+0.0)
     | > avg_loss_disc_real_4: 0.27198541164398193 (+0.0)
     | > avg_loss_disc_real_5: 0.25981926918029785 (+0.0)
     | > avg_loss_0: 2.4839155673980713 (+0.0)
     | > avg_loss_gen: 2.7426869869232178 (+0.0)
     | > avg_loss_kl: 3.109083414077759 (+0.0)
     | > avg_loss_feat: 5.6957902908325195 (+0.0)
     | > avg_loss_mel: 26.74468231201172 (+0.0)
     | > avg_loss_duration: 1.7994561195373535 (+0.0)
     | > avg_loss_1: 40.09170150756836 (+0.0)


 > EPOCH: 999/1000
 --> output/run-July-27-2023_05+40PM-0000000

 > TRAINING (2023-07-28 00:41:28) 

 > EVALUATION 


  --> EVAL PERFORMANCE
     | > avg_loader_time: 0.033222675323486

 | > Synthesizing test sentences.



  --> EVAL PERFORMANCE
     | > avg_loader_time: 0.03322267532348633 (+0.0)
     | > avg_loss_disc: 2.490471839904785 (+0.0)
     | > avg_loss_disc_real_0: 0.17550542950630188 (+0.0)
     | > avg_loss_disc_real_1: 0.19935698807239532 (+0.0)
     | > avg_loss_disc_real_2: 0.23585794866085052 (+0.0)
     | > avg_loss_disc_real_3: 0.2190139889717102 (+0.0)
     | > avg_loss_disc_real_4: 0.2575894892215729 (+0.0)
     | > avg_loss_disc_real_5: 0.24543151259422302 (+0.0)
     | > avg_loss_0: 2.490471839904785 (+0.0)
     | > avg_loss_gen: 2.1211230754852295 (+0.0)
     | > avg_loss_kl: 3.2888481616973877 (+0.0)
     | > avg_loss_feat: 4.261801242828369 (+0.0)
     | > avg_loss_mel: 25.429506301879883 (+0.0)
     | > avg_loss_duration: 1.7840980291366577 (+0.0)
     | > avg_loss_1: 36.885379791259766 (+0.0)



In [3]:
import os
os.path.exists('/root/tts-output/SethVoice/TTS/output/run-July-27-2023_05+40PM-0000000/config.json')

True

In [4]:
from TTS.api import Synthesizer

tts = Synthesizer(tts_checkpoint="../TTS/output/run-July-27-2023_05+40PM-0000000/best_model_7088.pth", tts_config_path="../TTS/output/run-July-27-2023_05+40PM-0000000/config.json")

#tts = TTS(model_name="/root/tts-output/run-July-26-2023_12+16AM-0000000/best_model_1908.pth", progress_bar=True, gpu=True)

 > Using model: vits
 > Setting up Audio Processor...
 | > sample_rate:22050
 | > resample:False
 | > num_mels:80
 | > log_func:np.log10
 | > min_level_db:0
 | > frame_shift_ms:None
 | > frame_length_ms:None
 | > ref_level_db:None
 | > fft_size:1024
 | > power:None
 | > preemphasis:0.0
 | > griffin_lim_iters:None
 | > signal_norm:None
 | > symmetric_norm:None
 | > mel_fmin:0
 | > mel_fmax:None
 | > pitch_fmin:None
 | > pitch_fmax:None
 | > spec_gain:20.0
 | > stft_pad_mode:reflect
 | > max_norm:1.0
 | > clip_norm:True
 | > do_trim_silence:False
 | > trim_db:60
 | > do_sound_norm:False
 | > do_amp_to_db_linear:True
 | > do_amp_to_db_mel:True
 | > do_rms_norm:False
 | > db_level:None
 | > stats_path:None
 | > base:10
 | > hop_length:256
 | > win_length:1024


In [9]:
outputs = tts.tts(text="Hello mother! I am Seth's voice clone.")
tts.save_wav(outputs, "output.wav")

 > Text splitted to sentences.
['Hello mother!', "I am Seth's voice clone."]
 > Processing time: 0.6421911716461182
 > Real-time factor: 0.16857518255710602
